# NLI base results: Turkish-Gemma-9b-T1 (ytu-ce-cosmos/Turkish-Gemma-9b-T1)

Loads [yilmazzey/sdp2-nli](https://huggingface.co/datasets/yilmazzey/sdp2-nli) (snli_tr_1_1, multinli_tr_1_1, trglue_mnli) and runs **test-only** evaluation with this model.

9B generative LLM (Gemma-2 based, Turkish instruction-tuned with reasoning/thinking). Zero-shot prompted NLI evaluation (no fine-tuning). Expect variable but potentially strong performance due to Turkish adaptation. Outputs parsed to 0=entailment, 1=neutral, 2=contradiction.

**Splits:** snli → test; multinli → validation_matched/mismatched; trglue → test_matched/test_mismatched. **Metrics:** Accuracy, macro F1, per-class F1, confusion matrix (CSV + plot).

In [1]:

!pip install -q -U transformers datasets accelerate scikit-learn tqdm

   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 10.4/10.4 MB 215.8 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 520.7/520.7 kB 70.8 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 8.9/8.9 MB 77.5 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 47.6/47.6 MB 15.4 MB/s eta 0:00:00


In [2]:
REPO_ID = "yilmazzey/sdp2-nli"
CONFIGS = ["snli_tr_1_1", "multinli_tr_1_1", "trglue_mnli"]
MODEL_ID = "ytu-ce-cosmos/Turkish-Gemma-9b-T1"
NUM_LABELS = 3  # entailment, neutral, contradiction
RESULTS_DIR = "results"
# Lower to 8-16 if GPU memory low (9B model is heavy). If CPU only, expect very slow run.
BATCH_SIZE = 32
EVAL_SPLITS = {
    "snli_tr_1_1": ["test"],
    "multinli_tr_1_1": ["validation_matched", "validation_mismatched"],
    "trglue_mnli": ["test_matched", "test_mismatched"],
}

In [3]:
# Colab: uncomment and run once to install/upgrade (Runtime -> Change runtime type -> GPU)
# !pip install -q -U transformers datasets accelerate scikit-learn tqdm

import json
import random
from collections import Counter
from pathlib import Path

import numpy as np
import torch
from datasets import load_dataset
from sklearn.metrics import accuracy_score, confusion_matrix, f1_score
from tqdm import tqdm
from transformers import pipeline

try:
    import matplotlib.pyplot as plt
    import seaborn as sns
    HAS_PLOT = True
except ImportError:
    HAS_PLOT = False

LABEL_NAMES = ["entailment", "neutral", "contradiction"]

# Colab: confirm GPU (e.g. Tesla T4 / A100)
if torch.cuda.is_available():
    print("GPU:", torch.cuda.get_device_name(0))
else:
    print("No GPU; 9B model will be very slow on CPU.")

SEED = 42
random.seed(SEED)
np.random.seed(SEED)
torch.manual_seed(SEED)
if torch.cuda.is_available():
    torch.cuda.manual_seed_all(SEED)
    torch.backends.cudnn.deterministic = True
    torch.backends.cudnn.benchmark = False

GPU: NVIDIA RTX PRO 6000 Blackwell Server Edition


In [4]:
# Load all three dataset configs
datasets = {}
for cfg in CONFIGS:
    print(f"Loading {REPO_ID} :: {cfg} ...")
    datasets[cfg] = load_dataset(REPO_ID, cfg)
    print("  splits:", list(datasets[cfg].keys()))

Loading yilmazzey/sdp2-nli :: snli_tr_1_1 ...


/usr/local/lib/python3.12/dist-packages/huggingface_hub/utils/_auth.py:94: UserWarning: 
The secret `HF_TOKEN` does not exist in your Colab secrets.
To authenticate with the Hugging Face Hub, create a token in your settings tab (https://huggingface.co/settings/tokens), set it as secret in your Google Colab and restart your session.
You will be able to reuse this secret in all of your notebooks.
Please note that authentication is recommended but still optional to access public models or datasets.
  warnings.warn(


README.md: 0.00B [00:00, ?B/s]

snli_tr_1_1/train-00000-of-00001.parquet:   0%|          | 0.00/25.4M [00:00<?, ?B/s]

snli_tr_1_1/validation-00000-of-00001.pa(…):   0%|          | 0.00/558k [00:00<?, ?B/s]

...

Generating validation_matched split:   0%|          | 0/9050 [00:00<?, ? examples/s]

Generating validation_mismatched split:   0%|          | 0/9200 [00:00<?, ? examples/s]

Generating test_matched split:   0%|          | 0/9008 [00:00<?, ? examples/s]

Generating test_mismatched split:   0%|          | 0/9217 [00:00<?, ? examples/s]

  splits: ['train', 'validation_matched', 'validation_mismatched', 'test_matched', 'test_mismatched']


In [5]:
print("Loading model and tokenizer (9B params; first run may download ~18GB and take several minutes)...")
generator = pipeline(
    "text-generation",
    model=MODEL_ID,
    device=0 if torch.cuda.is_available() else -1,
    torch_dtype=torch.bfloat16 if torch.cuda.is_available() else torch.float32,
    trust_remote_code=True,
    model_kwargs={"low_cpu_mem_usage": True},
)
if hasattr(generator.tokenizer, "pad_token") and generator.tokenizer.pad_token is None:
    generator.tokenizer.pad_token = generator.tokenizer.eos_token
print("Model loaded.")

Loading model and tokenizer (9B params; first run may download ~18GB and take several minutes)...


config.json:   0%|          | 0.00/853 [00:00<?, ?B/s]

`torch_dtype` is deprecated! Use `dtype` instead!


model.safetensors.index.json: 0.00B [00:00, ?B/s]

Fetching 4 files:   0%|          | 0/4 [00:00<?, ?it/s]

...

generation_config.json:   0%|          | 0.00/223 [00:00<?, ?B/s]

tokenizer_config.json: 0.00B [00:00, ?B/s]

tokenizer.json:   0%|          | 0.00/34.4M [00:00<?, ?B/s]

special_tokens_map.json:   0%|          | 0.00/644 [00:00<?, ?B/s]

Model loaded.


In [6]:
def nli_prompt(premise, hypothesis):
    return [
        {"role": "system", "content": "Sen doğal dil çıkarımı için yardımcı bir asistansın. Premise ve hypothesis arasındaki ilişkiyi sadece tek kelimeyle cevapla: entailment, neutral veya contradiction. Başka hiçbir şey yazma."},
        {"role": "user", "content": f"Premise: {premise}\nHypothesis: {hypothesis}\nLabel:"}
    ]

def parse_generated_label(gen_text, formatted_prompt):
    continuation = gen_text[len(formatted_prompt):].strip().lower()
    if not continuation:
        return 1
    first_word = continuation.split()[0].rstrip('.,!?;:')
    label_map = {"entailment": 0, "neutral": 1, "contradiction": 2,
                 "içerme": 0, "tarafsız": 1, "nötr": 1, "çelişki": 2}
    return label_map.get(first_word, 1)

def run_prompted_inference(ds):
    premises = list(ds["premise"])
    hypotheses = list(ds["hypothesis"])
    labels = list(ds["label"])
    n = len(ds)
    y_pred = []
    all_gens = []   # full debug

    for start in tqdm(range(0, n, BATCH_SIZE), desc="Inference"):
        batch_prompts = [nli_prompt(p, h) for p, h in zip(premises[start:start+BATCH_SIZE], hypotheses[start:start+BATCH_SIZE])]
        formatted = generator.tokenizer.apply_chat_template(batch_prompts, tokenize=False, add_generation_prompt=True)

        out = generator(
            formatted,
            max_new_tokens=5,      # strict
            do_sample=False,
            pad_token_id=generator.tokenizer.pad_token_id or generator.tokenizer.eos_token_id,
            max_length=None,
        )
        all_gens.extend(out)

        for gen in out:
            parsed = parse_generated_label(gen[0]["generated_text"], formatted[all_gens.index(gen) % len(formatted)])
            y_pred.append(parsed)

    y_true = np.array(labels, dtype=np.int64)
    y_pred = np.array(y_pred, dtype=np.int64)

    print("\n=== DEBUG SAMPLES ===")
    for i in range(min(5, n)):
        print(f"Sample {i}: {all_gens[i][0]['generated_text'][-150:]} → Parsed: {y_pred[i]}")

    print("True dist:", dict(Counter(y_true)))
    print("Pred dist:", dict(Counter(y_pred)))
    return y_true, y_pred

In [7]:
def compute_metrics(y_true, y_pred):
    acc = float(accuracy_score(y_true, y_pred))
    f1_macro = float(f1_score(y_true, y_pred, average="macro", zero_division=0))
    f1_per_class = f1_score(y_true, y_pred, average=None, zero_division=0)
    f1_per_class = {LABEL_NAMES[i]: float(f1_per_class[i]) for i in range(NUM_LABELS)}
    cm = confusion_matrix(y_true, y_pred)
    out = {"accuracy": acc, "f1_macro": f1_macro, "f1_per_class": f1_per_class}
    return out, cm


def save_confusion_plot(cm, path):
    if not HAS_PLOT:
        return
    fig, ax = plt.subplots(figsize=(6, 5))
    sns.heatmap(cm, annot=True, fmt="d", xticklabels=LABEL_NAMES, yticklabels=LABEL_NAMES, ax=ax)
    ax.set_xlabel("Predicted")
    ax.set_ylabel("True")
    plt.tight_layout()
    plt.savefig(path)
    plt.close()

In [8]:
Path(RESULTS_DIR).mkdir(parents=True, exist_ok=True)
all_metrics = {}

for config_name in CONFIGS:
    ds_dict = datasets[config_name]
    split_names = EVAL_SPLITS[config_name]
    all_metrics[config_name] = {}

    for split_name in split_names:
        if split_name not in ds_dict:
            print(f"  Skip {config_name}/{split_name} (missing)")
            continue
        ds = ds_dict[split_name]
        print(f"Evaluating {config_name} / {split_name} ...")
        y_true, y_pred = run_prompted_inference(ds)
        metrics, cm = compute_metrics(y_true, y_pred)
        all_metrics[config_name][split_name] = metrics

        cm_path = Path(RESULTS_DIR) / f"confusion_{config_name}_{split_name}.csv"
        np.savetxt(cm_path, cm, fmt="%d", delimiter=",")
        save_confusion_plot(cm, Path(RESULTS_DIR) / f"confusion_{config_name}_{split_name}.png")

        print(f"  accuracy={metrics['accuracy']:.4f}, f1_macro={metrics['f1_macro']:.4f}")

with open(Path(RESULTS_DIR) / "metrics.json", "w") as f:
    json.dump(all_metrics, f, indent=2)
print(f"Saved {RESULTS_DIR}/metrics.json")

Evaluating snli_tr_1_1 / test ...


Görüntülenen çıkış son 5000 satıra kısaltıldı.
Both `max_new_tokens` (=5) and `max_length`(=20) seem to have been set. `max_new_tokens` will take precedence. Please refer to the documentation for more information. (https://huggingface.co/docs/transformers/main/en/main_classes/text_generation)
Both `max_new_tokens` (=5) and `max_length`(=20) seem to have been set. `max_new_tokens` will take precedence. Please refer to the documentation for more information. (https://huggingface.co/docs/transformers/main/en/main_classes/text_generation)
Both `max_new_tokens` (=5) and `max_length`(=20) seem to have been set. `max_new_tokens` will take precedence. Please refer to the documentation for more information. (https://huggingface.co/docs/transformers/main/en/main_classes/text_generation)
Both `max_new_tokens` (=5) and `max_length`(=20) seem to have been set. `max_new_tokens` will take precedence. Please refer to the documentation for more information. (https://huggingface.co/docs/transformers/mai


=== DEBUG SAMPLES ===
Sample 0: kılar söylerken kitlelere şarkı söyler.
Hypothesis: Kilisenin tavanında çatlaklar var.
Label:<end_of_turn>
<start_of_turn>model
<think>
Hmm, kullanıcı → Parsed: 1
Sample 1: an neşeli şarkılar söylerken kitlelere şarkı söyler.
Hypothesis: Kilise şarkıyla dolu.
Label:<end_of_turn>
<start_of_turn>model
<think>
Hmm, kullanıcı → Parsed: 1
Sample 2: söylerken kitlelere şarkı söyler.
Hypothesis: Beyzbol maçında şarkı söyleyen bir koro.
Label:<end_of_turn>
<start_of_turn>model
<think>
Hmm, kullanıcı → Parsed: 1
Sample 3: örtüsü, mavi gömlekli ve çok büyük bir sırıtış olan bir kadın.
Hypothesis: Kadın genç.
Label:<end_of_turn>
<start_of_turn>model
<think>
Hmm, kullanıcı → Parsed: 1
Sample 4: ü, mavi gömlekli ve çok büyük bir sırıtış olan bir kadın.
Hypothesis: Kadın çok mutlu.
Label:<end_of_turn>
<start_of_turn>model
<think>
Hmm, kullanıcı → Parsed: 1
True dist: {np.int64(1): 3219, np.int64(0): 3368, np.int64(2): 3237}
Pred dist: {np.int64(1): 9824}
  accuracy=0

Görüntülenen çıkış son 5000 satıra kısaltıldı.
Both `max_new_tokens` (=5) and `max_length`(=20) seem to have been set. `max_new_tokens` will take precedence. Please refer to the documentation for more information. (https://huggingface.co/docs/transformers/main/en/main_classes/text_generation)
Both `max_new_tokens` (=5) and `max_length`(=20) seem to have been set. `max_new_tokens` will take precedence. Please refer to the documentation for more information. (https://huggingface.co/docs/transformers/main/en/main_classes/text_generation)
Both `max_new_tokens` (=5) and `max_length`(=20) seem to have been set. `max_new_tokens` will take precedence. Please refer to the documentation for more information. (https://huggingface.co/docs/transformers/main/en/main_classes/text_generation)
Both `max_new_tokens` (=5) and `max_length`(=20) seem to have been set. `max_new_tokens` will take precedence. Please refer to the documentation for more information. (https://huggingface.co/docs/transformers/mai


=== DEBUG SAMPLES ===
Sample 0: e: Yeni haklar yeterince güzel.
Hypothesis: Herkes gerçekten en yeni faydaları seviyor
Label:<end_of_turn>
<start_of_turn>model
<think>
Hmm, kullanıcı → Parsed: 1
Sample 1: banını içerir.
Hypothesis: Web sitesinde yer alan Hükümet Yürütme makaleleri aranamaz.
Label:<end_of_turn>
<start_of_turn>model
<think>
Hmm, kullanıcı → Parsed: 1
Sample 2: unlukla ondan hoşlanıyorum, ama yine de birinin onu dövdüğünü görmekten zevk alıyorum.
Label:<end_of_turn>
<start_of_turn>model
<think>
Hmm, kullanıcı → Parsed: 1
Sample 3: ğu sürece.
Hypothesis: En sevdiğim restoranlar her zaman evimden en az yüz mil uzakta.
Label:<end_of_turn>
<start_of_turn>model
<think>
Hmm, kullanıcı → Parsed: 1
Sample 4: r
Premise: Bilmiyorum. Çok fazla kamp yapıyor musun?
Hypothesis: Tam olarak biliyorum.
Label:<end_of_turn>
<start_of_turn>model
<think>
Hmm, kullanıcı → Parsed: 1
True dist: {np.int64(1): 3123, np.int64(2): 3211, np.int64(0): 3475}
Pred dist: {np.int64(1): 9809}
  accuracy=0

...


=== DEBUG SAMPLES ===
Sample 0: a yardımcı oldu.
Hypothesis: Katkılarınızın öğrencilerimizin eğitimine faydası olmadı.
Label:<end_of_turn>
<start_of_turn>model
<think>
Hmm, kullanıcı → Parsed: 1
Sample 1: rli bir konudur.
Hypothesis: Sözlükler gerçekten iki benzersiz ikame alıştırmalarıdır.
Label:<end_of_turn>
<start_of_turn>model
<think>
Hmm, kullanıcı → Parsed: 1
Sample 2: ir Toskana yemeği servis ediyoruz.
Hypothesis: Biz Florentine Terine bir yemek servis.
Label:<end_of_turn>
<start_of_turn>model
<think>
Hmm, kullanıcı → Parsed: 1
Sample 3: r mektup yazdık.
Hypothesis: Carl Newton ve ben seninle daha önce hiç temasa geçmedik.
Label:<end_of_turn>
<start_of_turn>model
<think>
Hmm, kullanıcı → Parsed: 1
Sample 4:  henüz ne olduğunu bilmiyorum.
Hypothesis: Dünya'da neden yaşadığımı henüz bilmiyorum.
Label:<end_of_turn>
<start_of_turn>model
<think>
Hmm, kullanıcı → Parsed: 1
True dist: {np.int64(2): 3240, np.int64(0): 3456, np.int64(1): 3129}
Pred dist: {np.int64(1): 9825}
  accuracy=0

Görüntülenen çıkış son 5000 satıra kısaltıldı.
Both `max_new_tokens` (=5) and `max_length`(=20) seem to have been set. `max_new_tokens` will take precedence. Please refer to the documentation for more information. (https://huggingface.co/docs/transformers/main/en/main_classes/text_generation)
Both `max_new_tokens` (=5) and `max_length`(=20) seem to have been set. `max_new_tokens` will take precedence. Please refer to the documentation for more information. (https://huggingface.co/docs/transformers/main/en/main_classes/text_generation)
Both `max_new_tokens` (=5) and `max_length`(=20) seem to have been set. `max_new_tokens` will take precedence. Please refer to the documentation for more information. (https://huggingface.co/docs/transformers/main/en/main_classes/text_generation)
Both `max_new_tokens` (=5) and `max_length`(=20) seem to have been set. `max_new_tokens` will take precedence. Please refer to the documentation for more information. (https://huggingface.co/docs/transformers/mai


=== DEBUG SAMPLES ===
Sample 0: lazım? Son düzenleyen: Moderatör: 16 Mayıs 2021.
Hypothesis: Su, hayat için önemlidir.
Label:<end_of_turn>
<start_of_turn>model
<think>
Hmm, kullanıcı → Parsed: 1
Sample 1: gal gibi yürek lazım.
Hypothesis: Savcının fitne fesat içinde olduğu iddia edilebilir.
Label:<end_of_turn>
<start_of_turn>model
<think>
Hmm, kullanıcı → Parsed: 1
Sample 2:  Tatil sırasında evleri korumak için en etkili yöntem, elektronik güvenlik sistemidir.
Label:<end_of_turn>
<start_of_turn>model
<think>
Hmm, kullanıcı → Parsed: 1
Sample 3: aphary Hectopat Katılım 2 Eylül 2019 Mesajlar 4.
Hypothesis: Facebook 2004'te kuruldu.
Label:<end_of_turn>
<start_of_turn>model
<think>
Hmm, kullanıcı → Parsed: 1
Sample 4: LSAN'ın 'CENKER Takın ve Tek-Er Komuta Kontrol Sistemi' TSK'yı öne geçirecek değildir.
Label:<end_of_turn>
<start_of_turn>model
<think>
Hmm, kullanıcı → Parsed: 1
True dist: {np.int64(1): 3138, np.int64(2): 2946, np.int64(0): 2924}
Pred dist: {np.int64(1): 9008}
  accuracy=0

Görüntülenen çıkış son 5000 satıra kısaltıldı.
Both `max_new_tokens` (=5) and `max_length`(=20) seem to have been set. `max_new_tokens` will take precedence. Please refer to the documentation for more information. (https://huggingface.co/docs/transformers/main/en/main_classes/text_generation)
Both `max_new_tokens` (=5) and `max_length`(=20) seem to have been set. `max_new_tokens` will take precedence. Please refer to the documentation for more information. (https://huggingface.co/docs/transformers/main/en/main_classes/text_generation)
Both `max_new_tokens` (=5) and `max_length`(=20) seem to have been set. `max_new_tokens` will take precedence. Please refer to the documentation for more information. (https://huggingface.co/docs/transformers/main/en/main_classes/text_generation)
Both `max_new_tokens` (=5) and `max_length`(=20) seem to have been set. `max_new_tokens` will take precedence. Please refer to the documentation for more information. (https://huggingface.co/docs/transformers/mai


=== DEBUG SAMPLES ===
Sample 0: ruyucu tanrısına dönüştü.
Hypothesis: Kiraz ağaçları Japonya'da yaygın olarak yetişir.
Label:<end_of_turn>
<start_of_turn>model
<think>
Hmm, kullanıcı → Parsed: 1
Sample 1: ığı da bu şekilde azalacak.
Hypothesis: Ev cari açığı, 2018 ile 2020 arasında düşecek.
Label:<end_of_turn>
<start_of_turn>model
<think>
Hmm, kullanıcı → Parsed: 1
Sample 2: Marc Jacobs, Pre-Fall koleksiyonunu sergilemek için bilinen süper modelleri çağırmadı.
Label:<end_of_turn>
<start_of_turn>model
<think>
Hmm, kullanıcı → Parsed: 1
Sample 3: rmesi lazım.
Hypothesis: İfade, kimin cevap vereceği konusunda kesin bir karar vermez.
Label:<end_of_turn>
<start_of_turn>model
<think>
Hmm, kullanıcı → Parsed: 1
Sample 4: thesis: Cilt yaşlanmasıyla ilgili sorunlara yönelik ürünler daha popüler hale geliyor.
Label:<end_of_turn>
<start_of_turn>model
<think>
Hmm, kullanıcı → Parsed: 1
True dist: {np.int64(1): 3043, np.int64(0): 3101, np.int64(2): 3073}
Pred dist: {np.int64(1): 9217}
  accuracy=0

In [9]:
# Summary: per config/split
for config_name, splits in all_metrics.items():
    for split_name, m in splits.items():
        print(f"{config_name} / {split_name}: acc={m['accuracy']:.4f}, F1_macro={m['f1_macro']:.4f}, F1_per_class={m['f1_per_class']}")

snli_tr_1_1 / test: acc=0.3277, F1_macro=0.1645, F1_per_class={'entailment': 0.0, 'neutral': 0.49359809859694853, 'contradiction': 0.0}
multinli_tr_1_1 / validation_matched: acc=0.3184, F1_macro=0.1610, F1_per_class={'entailment': 0.0, 'neutral': 0.4829879369007114, 'contradiction': 0.0}
multinli_tr_1_1 / validation_mismatched: acc=0.3185, F1_macro=0.1610, F1_per_class={'entailment': 0.0, 'neutral': 0.48309402501157944, 'contradiction': 0.0}
trglue_mnli / test_matched: acc=0.3484, F1_macro=0.1722, F1_per_class={'entailment': 0.0, 'neutral': 0.5167133212580274, 'contradiction': 0.0}
trglue_mnli / test_mismatched: acc=0.3302, F1_macro=0.1655, F1_per_class={'entailment': 0.0, 'neutral': 0.4964110929853181, 'contradiction': 0.0}


In [10]:
import shutil
from google.colab import files

# Define the directory to be zipped
output_filename = 'results_archive'
shutil.make_archive(output_filename, 'zip', RESULTS_DIR)

# Download the zipped file
files.download(f'{output_filename}.zip')

<IPython.core.display.Javascript object>

<IPython.core.display.Javascript object>